In [ ]:
%pip install awswrangler pycaret[full]
# conda install -c nvidia -c rapidsai py-xgboost
%pip install xgboost
%pip install mlflow

In [1]:
# import awswrangler as wr
import pandas as pd
import numpy as np
# import boto3
# from sagemaker import get_execution_role
import datetime
import string
import random
from pycaret.classification import *

In [2]:
data = pd.read_csv('data/data_feature_eng.csv')
# print(data)

In [3]:
m_setup = setup(data=data, target='label', normalize=True, 
                   feature_interaction=False, 
                   feature_ratio=False,
                   trigonometry_features=False,
                   use_gpu=False)

In [ ]:
# max_depth = 트리 최대 깊이
# max_leaves = 트리 최대 리프
# subsample = row sampling
# colsample_bytree = column sampling 각 이터레이션에 사용되는 칼럼의 비율
# learning_rate = 러닝레이트
# 일반적으로 row sampling 보다는 column sampling이 모형성능과 학습시간에 더 큰 영향을 준다
# xgboost = create_model('xgboost', max_depth=16, max_leaves=255)
# xgboost = create_model('xgboost')
xgboost = create_model('xgboost', max_depth=8, max_leaves=256)
# best_model = compare_models(n_select=6)

In [5]:
# max leaves -> 2**(n-1), n = max_depth
params    = {'max_depth': [128, 64, 32],
             'max_leaves': [256, 1024, 4096],              
             'colsample_bytree':[0.2, 0.4, 0.6, 0.8, 1.0],
             'learning_rate':[0.05, 0.005]
             }#range(14,17)}
# tuned_xgboost = tune_model(xgboost, optimize='F1', custom_grid=params)
tuned_xgboost = tune_model(xgboost, optimize='Accuracy', custom_grid=params, tuner_verbose=3)
# tuned_xgboost = tune_model(xgboost, optimize='Kappa')

In [18]:
tuned_xgboost

Transformation Pipeline and Model Successfully Saved


XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
              colsample_bynode=1, colsample_bytree=0.6,
              enable_categorical=False, gamma=0, gpu_id=0, importance_type=None,
              interaction_constraints='', learning_rate=0.05, max_delta_step=0,
              max_depth=64, max_leaves=1024, min_child_weight=1, missing=nan,
              monotone_constraints='()', n_estimators=100, n_jobs=-1,
              num_parallel_tree=1, objective='binary:logistic',
              predictor='auto', random_state=1504, reg_alpha=0, reg_lambda=1,
              scale_pos_weight=1, subsample=1, tree_method='gpu_hist',
              use_label_encoder=True, validate_parameters=1, ...)

In [18]:
# plot_model(tuned_dt, plot='auc')
evaluate_model(tuned_xgboost)

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Hyperparameters', 'param…

In [6]:
mdl = finalize_model(tuned_xgboost)
save_model(mdl, 'tuned_xgboost_0207')
# save_model(tuned_xgboost, 'tuned_xgboost_0207')

Transformation Pipeline and Model Successfully Saved


hum     d_hum    dd_hum      temp    d_temp   dd_temp      door  \
0     -1.945604 -2.290672  0.909558  2.232716  0.689506 -0.019712 -0.123705   
1      1.311485  0.005779  0.000629  0.923433  0.003051  0.717519 -0.123705   
2      1.028260 -0.431640  0.484373  1.709003  0.003051 -0.001014 -0.123705   
3     -1.308348  0.005779  0.000629 -1.171419  0.003051 -0.001014 -0.123705   
4      0.461810  0.005779 -0.569680  0.848617 -0.389210 -0.212032 -0.123705   
...         ...       ...       ...       ...       ...       ...       ...   
19436  1.240679 -1.634543  1.422582  0.960842  0.003051 -1.304522 -0.123705   
19437  0.249391  0.005779  0.000629 -0.797338  0.689506 -0.019712 -0.123705   
19438  0.391003  0.005779  0.000629 -0.872155  0.003051 -0.001014 -0.123705   
19439  1.099066  0.005779 -0.684251  0.698985 -0.977600  1.233045 -0.123705   
19440  1.311485  0.005779  0.000629  1.297514  0.003051 -0.001014 -0.123705   

         motion     illum      hour  ...  dayofweek_4  dayofweek_5  \
0     -0.074166 -0.624394  0.072370  ...          1.0          0.0   
1     -0.074166 -1.005454  1.230731  ...          0.0          0.0   
2     -0.074166 -0.243334  0.941141  ...          0.0          0.0   
3     -0.074166 -0.624394 -0.217220  ...          0.0          1.0   
4     -0.074166 -1.005454 -1.665171  ...          0.0          0.0   
...         ...       ...       ...  ...          ...          ...   
19436 -0.074166 -1.005454 -0.941195  ...          0.0          0.0   
19437 -0.074166 -0.624394 -0.362015  ...          0.0          0.0   
19438 -0.074166 -0.624394  1.665117  ...          0.0          0.0   
19439 -0.074166 -1.005454 -0.941195  ...          0.0          0.0   
19440 -0.074166  1.280906  0.361961  ...          0.0          0.0   

       dayofweek_6  month_10  month_11  month_8  month_9  label  Label   Score  
0              0.0       0.0       1.0      0.0      0.0    0.0    0.0  0.9851  
1              0.0       0.0       0.0      0.0      1.0    0.0    0.0  0.9941  
2              0.0       0.0       0.0      0.0      1.0    1.0    1.0  0.9728  
3              0.0       0.0       1.0      0.0      0.0    0.0    0.0  0.9958  
4              1.0       0.0       0.0      0.0      1.0    0.0    0.0  0.9958  
...            ...       ...       ...      ...      ...    ...    ...     ...  
19436          0.0       0.0       0.0      0.0      1.0    0.0    0.0  0.9947  
19437          0.0       0.0       1.0      0.0      0.0    0.0    0.0  0.9621  
19438          0.0       0.0       1.0      0.0      0.0    0.0    0.0  0.9953  
19439          0.0       0.0       0.0      0.0      1.0    0.0    0.0  0.9940  
19440          0.0       0.0       0.0      0.0      1.0    1.0    1.0  0.7373  

[19441 rows x 24 columns]

In [4]:
load_mdl = load_model('tuned_xgboost_0207')
prediction = predict_model(load_mdl, data=data.iloc[-10000:])
prediction = prediction.astype({'Label':'float64'})
prediction.info()
from pycaret.utils import check_metric
check_metric(prediction['Label'], prediction['label'], metric = 'F1')

Transformation Pipeline and Model Successfully Loaded
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 54800 to 64799
Data columns (total 15 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   label      10000 non-null  float64
 1   hum        10000 non-null  float64
 2   d_hum      10000 non-null  float64
 3   dd_hum     10000 non-null  float64
 4   temp       10000 non-null  float64
 5   d_temp     10000 non-null  float64
 6   dd_temp    10000 non-null  float64
 7   door       10000 non-null  float64
 8   motion     10000 non-null  float64
 9   illum      10000 non-null  float64
 10  dayofweek  10000 non-null  int64  
 11  month      10000 non-null  int64  
 12  hour       10000 non-null  int64  
 13  Label      10000 non-null  float64
 14  Score      10000 non-null  float32
dtypes: float32(1), float64(11), int64(3)
memory usage: 1.1 MB


0.9821